In [1]:
import pandas as pd
import numpy as np
import os, sys, json, argparse, pickle
import sumolib, traci
from tqdm import tqdm
from datetime import datetime
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_scr = os.path.join(path_root, 'scripts')
sys.path.append(path_scr)
from generate_signals import SignalGenerator

In [2]:
self = SignalGenerator(config_name='test_0731',
                       month=7,
                       day=31,
                       hour=9,
                       minute=5)

In [3]:
self.prepare_data()
self.process_history()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-5. 필요한 보조 객체들이 모두 준비되었습니다.
2. 신호이력 테이블을 변환합니다.


In [4]:
self.process_movement()


3. 이동류정보 테이블을 변환합니다.


In [5]:
self.make_histids()
self.get_signals()

4. 통합 테이블을 생성합니다.
5. 신호를 생성합니다.


In [6]:
self.present_time

1722384300

In [7]:
phases = pd.read_csv(os.path.join(self.path_tables, 'TL_IF_SIGL.csv'))
phases = phases.drop(columns=['FRST_REG_DT', 'RINGA_FLOW', 'RINGB_FLOW'])
phases = phases.rename(columns={
    'PHASE_DT':'start_unix','CRSRD_ID':'inter_no',
    'RINGA_PHASE':'phas_A', 'RINGB_PHASE':'phas_B',
    'MAP_MODE':'STOS_NO'
    })
isp2move_A = self.isp2move['A']
isp2move_B = self.isp2move['B']
phases['move_A'] = phases.apply(
    lambda row: int(isp2move_A.get((row.inter_no, row.STOS_NO, row.phas_A), -1)), axis=1)
phases['move_B'] = phases.apply(
    lambda row: int(isp2move_B.get((row.inter_no, row.STOS_NO, row.phas_B), -1)), axis=1)
phases['start_unix'] = phases['start_unix'].apply(lambda x:int(datetime.strptime(x, '%Y-%m-%d %H:%M:%S').timestamp()))
phases

start_unix  inter_no  phas_A  phas_B  STOS_NO  move_A  move_B
0      1722383926       436       2       2        0       8       3
1      1722383926       437       3       3        0       8       3
2      1722383926       438       1       1        0       6       2
3      1722383926       442       1       1        0       6       1
4      1722383926       443       1       1        0       6       2
...           ...       ...     ...     ...      ...     ...     ...
11095  1722385043       444       4       4        0      -1      -1
11096  1722385043       455       2       2        0      -1      -1
11097  1722385043       456       4       4        0      17      -1
11098  1722385043       457       3       3        0      17      17
11099  1722385043       458       2       2        0      17      17

[11100 rows x 7 columns]

In [8]:
fsecs = list(range(self.present_time - self.sim_timespan, self.present_time + 1, 5))

In [9]:
print(phases.start_unix.min())
print(phases.start_unix.max())
print(self.present_time)
print(fsecs[0])
print(fsecs[-1])

1722383926
1722385043
1722384300
1722384000
1722384300


In [10]:
for fsec in range(self.present_time - self.sim_timespan, self.present_time + 1, 5):
    # 1. 상태 테이블 조회해서 전체 데이터중 필요데이터(교차로번호, A링 현시번호, A링 이동류번호, B링 현시번호, B링 이동류번호)만 수집 : A
    moves = [group.iloc[-1:] for _, group in phases[phases.start_unix < fsec].groupby('inter_no')]
    if not moves:
        move = pd.DataFrame({
            'start_unix':[], 'inter_no':[], 'phas_A':[], 'phas_B':[],
            'STOS_NO':[], 'move_A':[], 'move_B':[]})
    else:
        move = pd.concat(moves)
    move = move.drop(columns='start_unix')
    # 2. 이력 테이블 조회해서 교차로별로 유닉스시간 최대인 데이터(교차로번호, 종료유닉스타임)만 수집 : B
    recent_histories = [group.iloc[-1:] for _, group in self.history[self.history['end_unix'] < fsec].groupby('inter_no')] # 교차로별로 유닉스시간이 최대인 행들

    if not recent_histories:
        rhistory = pd.DataFrame({'inter_no':[], 'end_unix':[]}) # recent history
    else:
        rhistory = pd.concat(recent_histories)
    recent_unix = rhistory[['inter_no', 'end_unix']]
    # 3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
    move = pd.merge(move, recent_unix, how='left', on='inter_no')
    move['end_unix'] = move['end_unix'].fillna(0).astype(int)
    # # 4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거
    move = move.rename(columns = {'end_unix':'start_unix'})
    # 5. 이동류 이력정보 READ
    #     - CSV 파일로 서버에 저장된 이동류정보를 읽어옴(파일이 없는 경우에는 데이터가 없는 프레임 D 생성)
    try:
        movement # movement가 존재할 경우 그걸 그대로 씀.
    except NameError: # movement가 존재하지 않는 경우 생성
        movement = pd.DataFrame()
    # 6. 이동류 이력정보 데이터테이블(D)에 C데이터 add
    movement = pd.concat([movement, move])
    # 7. D데이터 프레임에서 중복데이터 제거(교차로번호, 시작 유닉스타임, A링 현시번호, B링 현시번호 같은 행은 제거)
    movement = movement.drop_duplicates(['inter_no','phas_A','phas_B','start_unix'])
    # 8. D데이터 보관 시간 기준시간을 시작 유닉스 타임의 최대값 - self.subtractor // 2을 값으로 산출하고, 보관 시간 기준시간보다 작은 시작 유닉스 타임을 가진 행은 모두 제거(1시간 데이터만 보관)
    movement = movement[movement.start_unix > fsec - self.subtractor // 2]
movement


inter_no  phas_A  phas_B  STOS_NO  move_A  move_B  start_unix
6       455       1       1        0       6       2  1722383976
7       456       2       2        0       6       2  1722383967
1       437       1       1        0       6       2  1722384007
7       456       3       3        0       7      -1  1722383967
7       456       4       4        0      17      -1  1722383967
6       455       2       2        0      -1      -1  1722383976
8       457       1       1        0       6       2  1722384053
7       456       1       1        0       5       2  1722383967
1       437       2       2        0       5       1  1722384007
3       442       1       1        0       6       1  1722384098
8       457       2       2        0       5       1  1722384053
4       443       1       1        0       6       2  1722384102
1       437       3       3        0       8       3  1722384007
8       457       3       3        0      17      17  1722384053
3       442       2       2        0       6       2  1722384098
1       437       4       4        0       7       4  1722384007
3       442       3       3        0       5       2  1722384098
8       457       4       4        0       8       3  1722384053
3       442       4       4        0       7       4  1722384098
8       457       5       5        0       7       4  1722384053
1       437       1       1        0       6       2  1722384207
4       443       2       2        0       5       2  1722384102
8       457       1       1        0       6       2  1722384232
0       436       1       1        0       5       2  1722384236
3       442       5       5        0       8       3  1722384098
4       443       3       3        0       7      18  1722384102
8       457       2       2        0       5       1  1722384232
1       437       2       2        0       5       1  1722384207
3       442       6       6        0       8       3  1722384098
0       436       2       2        0       8       3  1722384236
3       442       1       1        0       6       1  1722384297
8       457       3       3        0      17      17  1722384232

In [11]:
phases

start_unix  inter_no  phas_A  phas_B  STOS_NO  move_A  move_B
0      1722383926       436       2       2        0       8       3
1      1722383926       437       3       3        0       8       3
2      1722383926       438       1       1        0       6       2
3      1722383926       442       1       1        0       6       1
4      1722383926       443       1       1        0       6       2
...           ...       ...     ...     ...      ...     ...     ...
11095  1722385043       444       4       4        0      -1      -1
11096  1722385043       455       2       2        0      -1      -1
11097  1722385043       456       4       4        0      17      -1
11098  1722385043       457       3       3        0      17      17
11099  1722385043       458       2       2        0      17      17

[11100 rows x 7 columns]

In [12]:
self.movement = pd.read_csv(os.path.join(self.path_tables, 'TL_IF_SIGL.csv'))
self.movement = self.movement.drop(columns=['FRST_REG_DT', 'RINGA_FLOW', 'RINGB_FLOW'])
self.movement = self.movement.rename(columns={
    'PHASE_DT':'start_unix','CRSRD_ID':'inter_no',
    'RINGA_PHASE':'phas_A', 'RINGB_PHASE':'phas_B',
    'MAP_MODE':'STOS_NO'
    })
isp2move_A = self.isp2move['A']
isp2move_B = self.isp2move['B']
self.movement['move_A'] = self.movement.apply(
    lambda row: int(isp2move_A.get((row.inter_no, row.STOS_NO, row.phas_A), -1)), axis=1)
self.movement['move_B'] = self.movement.apply(
    lambda row: int(isp2move_B.get((row.inter_no, row.STOS_NO, row.phas_B), -1)), axis=1)
self.movement['start_unix'] = pd.to_datetime(self.movement['start_unix'])
self.movement['start_unix'] = self.movement['start_unix'].apply(lambda x: int(x.timestamp()))


In [13]:
self.movement = pd.read_csv(os.path.join(self.path_tables, 'TL_IF_SIGL.csv'))
display(self.movement)
self.movement = self.movement.drop(columns=['FRST_REG_DT', 'RINGA_FLOW', 'RINGB_FLOW'])
display(self.movement)
self.movement = self.movement.rename(columns={
    'PHASE_DT':'start_unix','CRSRD_ID':'inter_no',
    'RINGA_PHASE':'phas_A', 'RINGB_PHASE':'phas_B',
    'MAP_MODE':'STOS_NO'
    })
display(self.movement)
isp2move_A = self.isp2move['A']
isp2move_B = self.isp2move['B']
self.movement['move_A'] = self.movement.apply(
    lambda row: int(isp2move_A.get((row.inter_no, row.STOS_NO, row.phas_A), -1)), axis=1)
self.movement['move_B'] = self.movement.apply(
    lambda row: int(isp2move_B.get((row.inter_no, row.STOS_NO, row.phas_B), -1)), axis=1)
display(self.movement)
self.movement['start_unix'] = pd.to_datetime(self.movement['start_unix'])
self.movement['start_unix'] = self.movement['start_unix'].apply(lambda x: int(x.timestamp()))
display(self.movement)

PHASE_DT  CRSRD_ID  RINGA_PHASE  RINGA_FLOW  RINGB_PHASE  \
0      2024-07-31 08:58:46       436            2           8            2   
1      2024-07-31 08:58:46       437            3           8            3   
2      2024-07-31 08:58:46       438            1           6            1   
3      2024-07-31 08:58:46       442            1           6            1   
4      2024-07-31 08:58:46       443            1           6            1   
...                    ...       ...          ...         ...          ...   
11095  2024-07-31 09:17:23       444            4           7            4   
11096  2024-07-31 09:17:23       455            2           1            2   
11097  2024-07-31 09:17:23       456            4          17            4   
11098  2024-07-31 09:17:23       457            3          17            3   
11099  2024-07-31 09:17:23       458            2          17            2   

       RINGB_FLOW  MAP_MODE                 FRST_REG_DT  
0               3         0  2024-07-31 08:58:46.799000  
1               3         0  2024-07-31 08:58:46.799000  
2               2         0  2024-07-31 08:58:46.799000  
3               1         0  2024-07-31 08:58:46.799000  
4               2         0  2024-07-31 08:58:46.799000  
...           ...       ...                         ...  
11095           4         0  2024-07-31 09:17:23.051000  
11096           1         0  2024-07-31 09:17:23.051000  
11097           1         0  2024-07-31 09:17:23.051000  
11098          17         0  2024-07-31 09:17:23.051000  
11099          17         0  2024-07-31 09:17:23.051000  

[11100 rows x 8 columns]

PHASE_DT  CRSRD_ID  RINGA_PHASE  RINGB_PHASE  MAP_MODE
0      2024-07-31 08:58:46       436            2            2         0
1      2024-07-31 08:58:46       437            3            3         0
2      2024-07-31 08:58:46       438            1            1         0
3      2024-07-31 08:58:46       442            1            1         0
4      2024-07-31 08:58:46       443            1            1         0
...                    ...       ...          ...          ...       ...
11095  2024-07-31 09:17:23       444            4            4         0
11096  2024-07-31 09:17:23       455            2            2         0
11097  2024-07-31 09:17:23       456            4            4         0
11098  2024-07-31 09:17:23       457            3            3         0
11099  2024-07-31 09:17:23       458            2            2         0

[11100 rows x 5 columns]

start_unix  inter_no  phas_A  phas_B  STOS_NO
0      2024-07-31 08:58:46       436       2       2        0
1      2024-07-31 08:58:46       437       3       3        0
2      2024-07-31 08:58:46       438       1       1        0
3      2024-07-31 08:58:46       442       1       1        0
4      2024-07-31 08:58:46       443       1       1        0
...                    ...       ...     ...     ...      ...
11095  2024-07-31 09:17:23       444       4       4        0
11096  2024-07-31 09:17:23       455       2       2        0
11097  2024-07-31 09:17:23       456       4       4        0
11098  2024-07-31 09:17:23       457       3       3        0
11099  2024-07-31 09:17:23       458       2       2        0

[11100 rows x 5 columns]

start_unix  inter_no  phas_A  phas_B  STOS_NO  move_A  move_B
0      2024-07-31 08:58:46       436       2       2        0       8       3
1      2024-07-31 08:58:46       437       3       3        0       8       3
2      2024-07-31 08:58:46       438       1       1        0       6       2
3      2024-07-31 08:58:46       442       1       1        0       6       1
4      2024-07-31 08:58:46       443       1       1        0       6       2
...                    ...       ...     ...     ...      ...     ...     ...
11095  2024-07-31 09:17:23       444       4       4        0      -1      -1
11096  2024-07-31 09:17:23       455       2       2        0      -1      -1
11097  2024-07-31 09:17:23       456       4       4        0      17      -1
11098  2024-07-31 09:17:23       457       3       3        0      17      17
11099  2024-07-31 09:17:23       458       2       2        0      17      17

[11100 rows x 7 columns]

start_unix  inter_no  phas_A  phas_B  STOS_NO  move_A  move_B
0      1722416326       436       2       2        0       8       3
1      1722416326       437       3       3        0       8       3
2      1722416326       438       1       1        0       6       2
3      1722416326       442       1       1        0       6       1
4      1722416326       443       1       1        0       6       2
...           ...       ...     ...     ...      ...     ...     ...
11095  1722417443       444       4       4        0      -1      -1
11096  1722417443       455       2       2        0      -1      -1
11097  1722417443       456       4       4        0      17      -1
11098  1722417443       457       3       3        0      17      17
11099  1722417443       458       2       2        0      17      17

[11100 rows x 7 columns]

In [14]:
display(self.movement)

start_unix  inter_no  phas_A  phas_B  STOS_NO  move_A  move_B
0      1722416326       436       2       2        0       8       3
1      1722416326       437       3       3        0       8       3
2      1722416326       438       1       1        0       6       2
3      1722416326       442       1       1        0       6       1
4      1722416326       443       1       1        0       6       2
...           ...       ...     ...     ...      ...     ...     ...
11095  1722417443       444       4       4        0      -1      -1
11096  1722417443       455       2       2        0      -1      -1
11097  1722417443       456       4       4        0      17      -1
11098  1722417443       457       3       3        0      17      17
11099  1722417443       458       2       2        0      17      17

[11100 rows x 7 columns]

In [15]:
self.process_movement()
self.make_histids()
self.get_signals()

3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.
5. 신호를 생성합니다.


In [16]:
import pandas as pd
import numpy as np

# 예제 DataFrame 생성
data = {
    'A': [1,        2,      np.nan, 4,      np.nan, 6],
    'B': [np.nan,   2,      3,      np.nan, 5,      6],
    'C': [1,        np.nan, np.nan, 4,      5,      6]
}
df = pd.DataFrame(data)

print("원본 DataFrame:")
display(df)

# 결측값을 앞의 값으로 채우기
# df_filled = df.fillna(method='ffill')
df_filled = df.ffill()#fillna(method='ffill')

print("\n결측값을 앞의 값으로 채운 DataFrame:")
display(df_filled)


원본 DataFrame:


A    B    C
0  1.0  NaN  1.0
1  2.0  2.0  NaN
2  NaN  3.0  NaN
3  4.0  NaN  4.0
4  NaN  5.0  5.0
5  6.0  6.0  6.0


결측값을 앞의 값으로 채운 DataFrame:


A    B    C
0  1.0  NaN  1.0
1  2.0  2.0  1.0
2  2.0  3.0  1.0
3  4.0  3.0  4.0
4  4.0  5.0  5.0
5  6.0  6.0  6.0

In [17]:
time_str = '2024-07-29 9:36:32'
time_dt = datetime.strptime(time_str, '%Y-%m-%d %H:%M:%S')
print(time_dt)
time_unix = int(time_dt.timestamp())
print(time_unix)
print(datetime.fromtimestamp(time_unix))

2024-07-29 09:36:32
1722213392
2024-07-29 09:36:32


In [18]:
self = SignalGenerator(config_name='test_0731',
                       month=7,
                       day=31,
                       hour=9,
                       minute=5)

In [19]:
self.load_networks()

1-1. 네트워크가 로드되었습니다.


In [20]:
self.load_tables()

1-2. 테이블들이 로드되었습니다.


In [21]:
print(self.history.end_unix.min())
print(self.history.end_unix.max())
print(self.present_time)
print(self.midnight)
print(self.next_day)

1722383967
1722385038
1722384300
1722351600
1722438000


In [22]:
# dura_As = [f'dura_A{i}' for i in range(1,9)]
# dura_Bs = [f'dura_B{i}' for i in range(1,9)]
# for i, row in self.plan.iterrows():
#     is_zero_A = (row[dura_As]==0).all()
#     is_zero_B = (row[dura_Bs]==0).all()
#     assert not (is_zero_A & is_zero_B)
#     if is_zero_B:
#         for j in range(1, 9):
#             self.plan.at[i, f'dura_B{j}'] = row[f'dura_A{j}']
#     if is_zero_A:
#         for j in range(1, 9):
#             self.plan.at[i, f'dura_A{j}'] = row[f'dura_B{j}']

In [23]:
self.prepare_auxiliaries()

1-5. 필요한 보조 객체들이 모두 준비되었습니다.


In [24]:
# valid_parent_ids = [self.inter2node[inter_no] for inter_no in set(self.history.inter_no)]
# invalid_parent_ids = [parent_id for parent_id in self.parent_ids if not parent_id in valid_parent_ids ]
# print(sorted(self.parent_ids))
# print(sorted(valid_parent_ids))
# print(sorted(invalid_parent_ids))
# invalid_child_ids = []
# for parent_id in invalid_parent_ids:
#     invalid_child_ids.extend(self.pa2ch[parent_id])
# print(sorted(invalid_child_ids))

# print()
# print()
# self.parent_ids = sorted(set(self.parent_ids) - set(invalid_parent_ids))
# self.node_ids = sorted(set(self.node_ids) - set(invalid_parent_ids))
# self.child_ids = sorted(set(self.child_ids) - set(invalid_child_ids))
# self.uturn_ids = sorted(set(self.uturn_ids) - set(invalid_child_ids))
# self.coord_ids = sorted(set(self.coord_ids) - set(invalid_child_ids))
# print(self.parent_ids)
# print(self.node_ids)
# print(self.child_ids)
# print(self.uturn_ids)
# print(self.coord_ids)

In [ ]:
sorted(inter_no for inter_no in set(self.history.inter_no))

In [ ]:
self.process_history()
sorted(inter_no for inter_no in set(self.rhistory.inter_no))

In [ ]:
sorted(inter_no for inter_no in set(self.rhists.inter_no))

In [ ]:
sorted(inter_no for inter_no in set(self.hrhists.inter_no))

In [ ]:
self.process_movement()
sorted(inter_no for inter_no in set(self.movement.inter_no))

In [ ]:
self.make_histids()

In [ ]:
sorted(inter_no for inter_no in set(self.movement_updated.inter_no))

In [ ]:
sorted(inter_no for inter_no in set(self.movedur.inter_no))

In [ ]:
sorted(inter_no for inter_no in set(self.histid.inter_no))

In [ ]:
sorted(node_id for node_id in set(self.histid.node_id))

In [ ]:
sorted(inter_no for inter_no in set(self.histids.inter_no))

In [ ]:
sorted(node_id for node_id in set(self.histids.node_id))

In [ ]:
self.histids

In [ ]:
self.set_timepoints()

In [ ]:
self.sigtable

In [ ]:
self.assign_red_yellow()

In [ ]:
self.make_tl_file()

In [ ]:
self.plan[self.plan.inter_no==455]

In [ ]:
self.SIGTABLE = []
node_id = self.node_ids[11]
print(node_id)
sig = self.sigtable.query('node_id==@node_id')
display(sig)
for i, row in sig.iterrows():
    inter_no = row.inter_no
    phas_A = row.phas_A
    phas_B = row.phas_B
    start_unix = row.start_unix
    prow = self.load_prow(inter_no, start_unix)[1].iloc[0]
    # 황색 및 적색시간 컬럼 생성
    red_A    = prow[f'red_A{phas_A}']
    yellow_A = prow[f'yellow_A{phas_A}']
    red_B    = prow[f'red_B{phas_B}']
    yellow_B = prow[f'yellow_B{phas_B}']
    sig.loc[i, ['red_A', 'red_B', 'yellow_A', 'yellow_B']] = red_A, red_B, yellow_A, yellow_B
display(sig)
sig = sig.astype({'red_A': int, 'red_B': int, 'yellow_A': int, 'yellow_B': int,
                'phas_A':str, 'phas_B':str})
sig = sig.drop(['move_A','move_B'], axis=1)
display(sig)

sig_A = sig[['start_unix', 'phas_A', 'duration', 'state_A', 'red_A', 'yellow_A']].reset_index(drop=True)
sig_B = sig[['start_unix', 'phas_B', 'duration', 'state_B', 'red_B', 'yellow_B']].reset_index(drop=True)
display(sig_A)
display(sig_B)


In [ ]:
self.parent_ids

In [ ]:
# csig_A = self.cumulate(sig_A, 'A')
sig = sig_A
alph = 'A'
csig = [] # cumulated sig
pre = pd.Series({f'phas_{alph}':None})

sig[f'phas_{alph}'] = sig[f'phas_{alph}'].astype(int)
# 만약 현시번호가 1로 일정하면 2현시를 가상으로 추가
if (sig[f'phas_{alph}']==1).all():
   sig_dup = sig.copy() 
   sig_dup[f'phas_{alph}'] = 2
   sig = pd.concat([sig, sig_dup]).sort_values(by=['start_unix', f'phas_{alph}'])

start_time = 0
elapsed = 0
for i, cur in sig.iterrows():
    start_unix = cur.start_unix
    
    # pre, nex
    if i != 0:
        pre = sig.iloc[i-1]
    
    if i != len(sig) - 1:
        nex = sig.iloc[i+1]
    
    # duration
    if cur[f'phas_{alph}'] == nex[f'phas_{alph}']:
        continue
    if cur[f'phas_{alph}'] == pre[f'phas_{alph}']:
        duration = cur.duration + pre.duration
    else:
        duration = cur.duration
    start_times = []
    states = []
    phases = []

    # red
    if i != 0:
        start_time += elapsed
        start_times.append(start_time)
        states.append(self.get_red(pre[f'state_{alph}'], cur[f'state_{alph}']))
        phases.append(f'{cur[f"phas_{alph}"]}r')

        elapsed = cur[f'red_{alph}']

    # green
    if i == 0:
        start_time = 0
    else:
        start_time += elapsed
    start_times.append(start_time)
    states.append(cur[f'state_{alph}'])
    phases.append(f'{cur[f"phas_{alph}"]}g')
    if i == 0:
        elapsed = duration - cur[f'yellow_{alph}']
    else:
        elapsed = duration - cur[f'yellow_{alph}'] - cur[f'red_{alph}']

    # yellow
    if i != len(sig) - 1:
        start_time += elapsed
        start_times.append(start_time)
        states.append(self.get_yellow(cur[f'state_{alph}'], nex[f'state_{alph}']))
        phases.append(f'{cur[f"phas_{alph}"]}y')
        elapsed = cur[f'yellow_{alph}']
    sig_ = pd.DataFrame({'start_time':start_times, f'phas_{alph}':phases, f'state_{alph}':states})
    sig_['start_unix'] = start_unix
    csig.append(sig_)
csig = pd.concat(csig).reset_index(drop=True)
csig


In [ ]:
self.SIGTABLE = []
node_id = self.node_ids[11]
print(node_id)
sig = self.sigtable.query('node_id==@node_id')
display(sig)
for i, row in sig.iterrows():
    inter_no = row.inter_no
    phas_A = row.phas_A
    phas_B = row.phas_B
    start_unix = row.start_unix
    prow = self.load_prow(inter_no, start_unix)[1].iloc[0]
    # 황색 및 적색시간 컬럼 생성
    red_A    = prow[f'red_A{phas_A}']
    yellow_A = prow[f'yellow_A{phas_A}']
    red_B    = prow[f'red_B{phas_B}']
    yellow_B = prow[f'yellow_B{phas_B}']
    sig.loc[i, ['red_A', 'red_B', 'yellow_A', 'yellow_B']] = red_A, red_B, yellow_A, yellow_B
display(sig)
sig = sig.astype({'red_A': int, 'red_B': int, 'yellow_A': int, 'yellow_B': int,
                'phas_A':str, 'phas_B':str})
sig = sig.drop(['move_A','move_B'], axis=1)
display(sig)

sig_A = sig[['start_unix', 'phas_A', 'duration', 'state_A', 'red_A', 'yellow_A']].reset_index(drop=True)
sig_B = sig[['start_unix', 'phas_B', 'duration', 'state_B', 'red_B', 'yellow_B']].reset_index(drop=True)
display(sig_A)
display(sig_B)

csig_A = self.cumulate(sig_A, 'A')
csig_B = self.cumulate(sig_B, 'B')
display(csig_A)
display(csig_B)

SIG = pd.merge(csig_A, csig_B, on=['start_time', 'start_unix'], how='outer')
display(SIG[:40])
SIG = SIG.sort_values(by='start_time').reset_index(drop=True)
SIG[['phas_A', 'state_A']] = SIG[['phas_A', 'state_A']].fillna(method='ffill')
SIG[['phas_B', 'state_B']] = SIG[['phas_B', 'state_B']].fillna(method='ffill')
SIG['phase'] = SIG['phas_A'] + "_" + SIG['phas_B']
SIG['node_id'] = node_id
SIG = SIG[['node_id', 'start_unix', 'start_time', 'phase', 'state_A', 'state_B']]
SIG['duration'] = SIG['start_time'].shift(-1) - SIG['start_time']
SIG = SIG[:-1]
SIG['duration'] = SIG['duration'].astype(int)
display(SIG[:40])
for row in SIG.itertuples():
    state = ''
    for a, b, in zip(row.state_A, row.state_B):
        if a == 'r':
            state += b
        elif b == 'r':
            state += a
        elif a == b:
            state += a
        else:
            raise ValueError(f"예상되지 않은 조합 발생: a={a}, b={b}")
    SIG.at[row.Index, 'state'] = state
display(SIG[:40])
SIG = SIG[SIG.duration!=0]
SIG = SIG.drop(columns=['start_time', 'state_A', 'state_B'])
display(SIG[:40])
self.SIGTABLE.append(SIG)


In [ ]:
self.offsets = {}
self.sigtable = []
sim_start = self.present_time - self.sim_timespan
print(self.present_time)
print(self.sim_timespan)

In [ ]:
node_id = '106231'
group = self.histids[self.histids.node_id==node_id]
min_start_unix = int(group['start_unix'].min())
min_start_unix

In [ ]:
node_id = '107587'
group = self.histids[self.histids.node_id==node_id]
series = group[group['start_unix'] < sim_start]['start_unix']
min_start_unix = int(group['start_unix'].min())
inter_no = self.node2inter[node_id]
_, prow = self.load_prow(inter_no, min_start_unix)
cycle = prow.iloc[0]['cycle']
lsbs = min_start_unix
print(lsbs, sim_start, cycle)
print(lsbs > sim_start)
print(type(lsbs), 'hello', type(sim_start))
while lsbs > sim_start:
    lsbs -= cycle
print(min_start_unix)


In [ ]:
self.offsets = {}
self.sigtable = []
sim_start = self.present_time - self.sim_timespan
for node_id, group in self.histids.groupby('node_id'):
    series = group[group['start_unix'] < sim_start]['start_unix']
    # lsbs : the last start_unix before sim_start
    if len(series):
        lsbs = series.max()
    else:
        min_start_unix = int(group['start_unix'].min())
        inter_no = self.node2inter[node_id]
        _, prow = self.load_prow(inter_no, min_start_unix)
        cycle = prow.iloc[0]['cycle']
        lsbs = min_start_unix
        while lsbs > sim_start:
            lsbs -= cycle
    self.offsets[node_id] = lsbs - sim_start
    group = group[group.start_unix >= lsbs]
    start_unixes = np.array(group.start_unix)
    start_unixes = np.sort(np.unique(start_unixes))[:self.node2num_cycles[node_id]]

    group = group[group.start_unix.isin(start_unixes)]
    self.sigtable.append(group)
self.sigtable = pd.concat(self.sigtable).reset_index(drop=True)
self.sigtable['phase_sumo'] = self.sigtable.groupby(['node_id', 'start_unix']).cumcount()

In [ ]:
sorted(inter_no for inter_no in set(self.sigtable.inter_no))

In [ ]:
sorted(node_id for node_id in set(self.sigtable.node_id))

In [ ]:
# 5-1
self.set_timepoints()

In [ ]:
self.SIGTABLE = []
for node_id in self.node_ids:
    sig = self.sigtable.query('node_id==@node_id')
    display(sig)
    for i, row in sig.iterrows():
        inter_no = row.inter_no
        phas_A = row.phas_A
        phas_B = row.phas_B
        start_unix = row.start_unix
        prow = self.load_prow(inter_no, start_unix)[1].iloc[0]
        red_A    = prow[f'red_A{phas_A}']
        yellow_A = prow[f'yellow_A{phas_A}']
        red_B    = prow[f'red_B{phas_B}']
        yellow_B = prow[f'yellow_B{phas_B}']
        sig.loc[i, ['red_A', 'red_B', 'yellow_A', 'yellow_B']] = red_A, red_B, yellow_A, yellow_B
    try:
        sig = sig.astype({'red_A': int, 'red_B': int, 'yellow_A': int, 'yellow_B': int,
                        'phas_A':str, 'phas_B':str})
        sig = sig.drop(['move_A','move_B'], axis=1)
    except:
        print(node_id)

    # sig_A = sig[['start_unix', 'phas_A', 'duration', 'state_A', 'red_A', 'yellow_A']].reset_index(drop=True)
    # sig_B = sig[['start_unix', 'phas_B', 'duration', 'state_B', 'red_B', 'yellow_B']].reset_index(drop=True)

    # csig_A = self.cumulate(sig_A, 'A')
    # csig_B = self.cumulate(sig_B, 'B')


In [ ]:
# 5-2. 적색 및 황색신호 부여
self.assign_red_yellow()